In [1]:
from masters_thesis.helper import api_get
from masters_thesis.definitions import REPO_SEARCH_DIR
import json

data = list(api_get("https://api.github.com/search/repositories?q=language:python&sort=stars&order=desc&per_page=100&page=1"))
with open(REPO_SEARCH_DIR / "python.json", "w") as f:
    json.dump(data, f, indent=2)

In [2]:
from masters_thesis.definitions import REPO_DIR

# dumping the repository data to repository folders
for repo in data[0]['items']:
    directory = REPO_DIR / repo['full_name']
    directory.mkdir(parents=True, exist_ok=True)
    with open(directory / "repo.json", "w") as f:
        json.dump(repo, f, indent=4)

In [8]:
from requests import get

specific_repo = REPO_DIR / "3b1b/manim"
with open (specific_repo / "repo.json") as f:
    repo_json = json.load(open(specific_repo / "repo.json"))
commits = list(api_get(repo_json['commits_url'].format(**{"/sha": "?per_page=100"})))
with open(specific_repo / "commits.json", "w") as f:
    json.dump(commits, f, indent=4)

In [9]:
issues = list(api_get(repo_json['issues_url'].format(**{"/number": "?per_page=100&state=all"})))
with open(specific_repo / "issues.json", "w") as f:
    json.dump(issues, f, indent=4)
issues

[{'items': [{'url': 'https://api.github.com/repos/3b1b/manim/issues/2030',
    'repository_url': 'https://api.github.com/repos/3b1b/manim',
    'labels_url': 'https://api.github.com/repos/3b1b/manim/issues/2030/labels{/name}',
    'comments_url': 'https://api.github.com/repos/3b1b/manim/issues/2030/comments',
    'events_url': 'https://api.github.com/repos/3b1b/manim/issues/2030/events',
    'html_url': 'https://github.com/3b1b/manim/issues/2030',
    'id': 1740554606,
    'node_id': 'I_kwDOAfLOx85nvsFu',
    'number': 2030,
    'title': 'Problem with standalone.cls',
    'user': {'login': 'Sleiman98',
     'id': 135544011,
     'node_id': 'U_kgDOCBQ8yw',
     'avatar_url': 'https://avatars.githubusercontent.com/u/135544011?v=4',
     'gravatar_id': '',
     'url': 'https://api.github.com/users/Sleiman98',
     'html_url': 'https://github.com/Sleiman98',
     'followers_url': 'https://api.github.com/users/Sleiman98/followers',
     'following_url': 'https://api.github.com/users/Sleiman

In [26]:
commits[0]['items'][50]

{'sha': '3c0d682efc39dfa6be4920a5cfa6fe8786835f24',
 'node_id': 'C_kwDOAfLOx9oAKDNjMGQ2ODJlZmMzOWRmYTZiZTQ5MjBhNWNmYTZmZTg3ODY4MzVmMjQ',
 'commit': {'author': {'name': 'Grant Sanderson',
   'email': 'grant@3blue1brown.com',
   'date': '2023-02-01T21:02:34Z'},
  'committer': {'name': 'Grant Sanderson',
   'email': 'grant@3blue1brown.com',
   'date': '2023-02-02T22:46:07Z'},
  'message': 'Change clicking behavior in InteractiveScene',
  'tree': {'sha': '305e7f6f89f1afda2202393b1c565ae5526b62bf',
   'url': 'https://api.github.com/repos/3b1b/manim/git/trees/305e7f6f89f1afda2202393b1c565ae5526b62bf'},
  'url': 'https://api.github.com/repos/3b1b/manim/git/commits/3c0d682efc39dfa6be4920a5cfa6fe8786835f24',
  'comment_count': 0,
  'verification': {'verified': False,
   'reason': 'unsigned',
   'signature': None,
   'payload': None}},
 'url': 'https://api.github.com/repos/3b1b/manim/commits/3c0d682efc39dfa6be4920a5cfa6fe8786835f24',
 'html_url': 'https://github.com/3b1b/manim/commit/3c0d682efc3

In [36]:
from datetime import datetime
from dateutil.parser import parse
from typing import Any

# created_at, updated_at, closed_at
created_at = parse(issues[0]['items'][0]['created_at'])
updated_at = parse(issues[0]['items'][0]['updated_at']) if issues[0]['items'][0]['updated_at'] else None
closed_at = parse(issues[0]['items'][0]['closed_at']) if issues[0]['items'][0]['closed_at'] else None

def issue_open_at(issue: dict[str, Any], date: datetime) -> bool:
    created_at = parse(issue['created_at'])
    closed_at = parse(issue['closed_at']) if issue['closed_at'] else None
    return created_at.replace(tzinfo=None) < date and (not closed_at or closed_at.replace(tzinfo=None) > date)

def number_of_issues_open(issues: dict[str, Any], date: datetime) -> int:
    return sum([1 for issue in issues if issue_open_at(issue, date)])

issue_open_at(issues[0]['items'][0], datetime(2023, 1, 1))
number_of_issues_open(issues[0]['items'], datetime(2023, 1, 1))

5

In [38]:
from typing import TypeVar

T = TypeVar("T")

def flatten(list: list[list[T]]) -> list[T]:
    """Flatten a list of lists"""
    return [item for sublist in list for item in sublist]


In [47]:
all_issues = flatten([response['items'] for response in issues])
all_commits = flatten([response['items'] for response in commits])
Y = [number_of_issues_open(all_issues, parse(commit['commit']['author']['date']).replace(tzinfo=None)) for commit in all_commits]
Y

TypeError: can't compare offset-naive and offset-aware datetimes